In [1]:
# Examen Integrador 

# Este codigo utiliza un sistema multiagente para modelar y simular la rotacion de un planeta al rededor de su sol.

# Autor: Alejandra Saldaña Rodriguez
# Matricula: A00838889
# Fecha: 05-09-2025

In [21]:
!pip install -q agentpy numpy matplotlib seaborn

In [29]:
import agentpy as ap
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [60]:
import socket
import json
s=socket.socket(socket.AF_INET, socket.SOCK_STREAM)
s.connect(("127.0.0.1", 1104))
from_server = s.recv(4096)
print ("Received from server: ",from_server.decode("ascii"))

Received from server:  I will send key


In [ ]:
class Planeta(ap.Agent):
    def setup(self):
        i = self.id - 1
        self.radio = self.model.p.radios[i] # distancia al sol
        self.velocidad = self.model.p.velocidades[i] # velocidad angular
        self.angulo = 0  # angulo inicial
        self.pos = (self.radio, 0)  # posición inicial

    def step(self):
        self.angulo += self.velocidad  # actualizar angulo
        # distancia al sol * cos()
        self.pos = (self.radio * np.cos(self.angulo),
                    self.radio * np.sin(self.angulo))
        # Envio de posiciones al servidor en Unity

        if s:
            try:
                posicion = '{{"id": {}, "x": {:.6f}, "y": {:.6f}}}'.format(
                        self.id, float(self.pos[0]), float(self.pos[1]))
                s.send(posicion.encode("ascii"))
                print(f"Enviado a Unity: {posicion}")
            except Exception as e:
                print(f"Error enviando posición a Unity: {e}")

class SistemaSolar(ap.Model):
    def setup(self):
        self.planetas = ap.AgentList(self, self.p.num_planetas, Planeta)

    def step(self):
        self.planetas.step()

    def update(self):
        self.record('posiciones', [p.pos for p in self.planetas])

# Parametros del modelo
params = {
    'steps': 600,
    'num_planetas': 1,
    'radios': [5],
    'velocidades': [0.1]
}

def draw_solar_system(m, ax):
    ax.clear()
    ax.set_xlim(-8, 8); ax.set_ylim(-8, 8)
    ax.set_aspect('equal')
    ax.set_xticks([]); ax.set_yticks([])
    ax.set_title(f"Sistema Solar | t = {m.t}")

    # Sol en el centro
    ax.add_patch(plt.Circle((0, 0), 0.4, color='yellow', zorder=2))

    # Planetas
    xs = [p.pos[0] for p in m.planetas]
    ys = [p.pos[1] for p in m.planetas]
    ax.scatter(xs, ys, s=80, c=['blue'], zorder=3, edgecolor='k')

# --- Ejecutamos animación ---
fig, ax = plt.subplots(figsize=(6,6))
model = SistemaSolar(params)
anim = ap.animate(model, fig, ax, draw_solar_system)

from IPython.display import HTML
HTML(anim.to_jshtml())

In [62]:
try:
    s.close()
except:
    pass